In [2]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service as ChromeService
from webdriver_manager.chrome import ChromeDriverManager
from selenium.common.exceptions import NoSuchElementException
from concurrent.futures import ThreadPoolExecutor
from time import sleep
import os
from selenium import webdriver
from selenium.webdriver.common.by import By
import time
import random
import pandas as pd
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.action_chains import ActionChains
import json


In [2]:

# Đường dẫn lưu bookmark
BOOKMARK_PATH = r"D:/du lieu o cu/HUTECH Courses/NCKH(thầy Hường)/E-Commerce-Data-Analysis/Data Scraping Selenium/bookmark.csv"

# Thư mục lưu file kết quả
OUTPUT_DIR = r"D:/du lieu o cu/HUTECH Courses/NCKH(thầy Hường)/E-Commerce-Data-Analysis/Data Scraping Selenium/Category_Files"
if not os.path.exists(OUTPUT_DIR):
    os.makedirs(OUTPUT_DIR)

def load_bookmark(file_path):
    """Load danh sách liên kết đã cào từ file."""
    if os.path.exists(file_path):
        return set(pd.read_csv(file_path)['Links'])
    return set()

def save_bookmark(file_path, links):
    """Lưu danh sách liên kết đã cào vào file (thêm mới, không ghi đè)."""
    if os.path.exists(file_path):
        existing_links = load_bookmark(file_path)
        links = links.union(existing_links)  # Gộp liên kết cũ và mới
    df = pd.DataFrame({'Links': list(links)})
    df.to_csv(file_path, index=False)

def save_all_store_links(store_links):
    """Lưu tất cả các đường link cửa hàng vào một file Excel chung."""
    output_file = os.path.join(OUTPUT_DIR, "store_links.xlsx")
    df = pd.DataFrame({'Links': list(store_links)})
    df.to_excel(output_file, index=False)
    print(f"Đã lưu tất cả các liên kết cửa hàng vào file: {output_file}")

def scroll_page(driver, scroll_count=10, pause=1.5, offset=25):
    """Cuộn trang để tải thêm nội dung."""
    total_height = driver.execute_script("return document.body.scrollHeight")
    scroll_step = (total_height - offset) / scroll_count
    for i in range(1, scroll_count + 1):
        driver.execute_script(f"window.scrollTo(0, {i * scroll_step});")
        time.sleep(pause)
    time.sleep(2)  # Đợi 2 giây sau khi cuộn xong

def collect_product_links(driver, product_links):
    """Thu thập liên kết sản phẩm từ trang hiện tại."""
    product_elements = driver.find_elements(By.CSS_SELECTOR, ".styles__ProductItemContainerStyled-sc-bszvl7-0 a.style__ProductLink-sc-139nb47-2")
    for elem in product_elements:
        link = elem.get_attribute("href")
        if link and link not in product_links:
            product_links.add(link)
            print(f"Collected {len(product_links)} links")

def crawl_category_links(driver, category_links):
    """
    Duyệt qua các danh mục và thu thập các liên kết cửa hàng.
    Thu thập liên tục cho đến khi không còn nút "Xem thêm" hoặc không có sản phẩm mới.
    """
    all_store_links = set()

    for idx, href in enumerate(category_links, start=1):
        print(f"\nĐang truy cập danh mục {idx}: {href}")
        driver.get(href)
        time.sleep(random.uniform(2, 5))

        category_product_links = set()

        while True:
            # Lưu số lượng hiện tại để so sánh sau khi thu thập
            current_count = len(category_product_links)
            collect_product_links(driver, category_product_links)
            
            # Nếu không có liên kết mới được thêm, có thể đã tải hết sản phẩm hiện tại
            if len(category_product_links) == current_count:
                try:
                    # Thử tìm và click nút "Xem thêm" nếu có
                    button = driver.find_element(By.CSS_SELECTOR, '[data-view-id="category_infinity_view.more"]')
                    ActionChains(driver).move_to_element(button).click(button).perform()
                    time.sleep(random.uniform(2, 3))
                    scroll_page(driver, scroll_count=5, pause=random.uniform(1, 1.5))
                except NoSuchElementException:
                    print("Nút 'Xem thêm' không còn hoặc đã tải hết sản phẩm.")
                    break
            else:
                # Nếu có sản phẩm mới được thêm, thử cuộn trang để kích hoạt load thêm
                scroll_page(driver, scroll_count=5, pause=random.uniform(1, 1.5))
        
        print(f"Danh mục {idx} hoàn thành. Thu thập được {len(category_product_links)} liên kết.")
        # Cập nhật tất cả liên kết cửa hàng với liên kết từ danh mục hiện tại
        all_store_links = all_store_links.union(category_product_links)

    return all_store_links

def main():
    # Tải bookmark đã cào (nếu có)
    crawled_links = load_bookmark(BOOKMARK_PATH)

    # Khởi tạo WebDriver
    driver = webdriver.Chrome()
    driver.get("https://tiki.vn")
    driver.implicitly_wait(5)

    # Tìm tất cả các thẻ <a> bên trong class "styles__StyledListItem-sc-w7gnxl-0"
    category_elements = driver.find_elements(By.CSS_SELECTOR, ".styles__StyledListItem-sc-w7gnxl-0 a")
    category_links = [link.get_attribute("href") for link in category_elements if link.get_attribute("href") not in crawled_links]
    category_links = category_links[1:26]  # Lấy danh mục từ 2 đến 26

    # Thu thập liên kết sản phẩm từ các danh mục và gom chúng lại
    all_store_links = crawl_category_links(driver, category_links)

    print("\nHoàn thành thu thập liên kết sản phẩm.")
    print(f"Tổng số liên kết thu thập được: {len(all_store_links)}")

    # Lưu tất cả các liên kết cửa hàng vào 1 file Excel chung
    save_all_store_links(all_store_links)

    # Nếu cần cập nhật bookmark thì lưu lại các liên kết danh mục đã cào (tuỳ chọn)
    save_bookmark(BOOKMARK_PATH, set(category_links))

    # Đóng trình duyệt
    driver.quit()

if __name__ == "__main__":
    main()



Đang truy cập danh mục 1: https://tiki.vn/nha-cua-doi-song/c1883
Collected 1 links
Collected 2 links
Collected 3 links
Collected 4 links
Collected 5 links
Collected 6 links
Collected 7 links
Collected 8 links
Collected 9 links
Collected 10 links
Collected 11 links
Collected 12 links
Collected 13 links
Collected 14 links
Collected 15 links
Collected 16 links
Collected 17 links
Collected 18 links
Collected 19 links
Collected 20 links
Collected 21 links
Collected 22 links
Collected 23 links
Collected 24 links
Collected 25 links
Collected 26 links
Collected 27 links
Collected 28 links
Collected 29 links
Collected 30 links
Collected 31 links
Collected 32 links
Collected 33 links
Collected 34 links
Collected 35 links
Collected 36 links
Collected 37 links
Collected 38 links
Collected 39 links
Collected 40 links
Collected 41 links
Collected 42 links
Collected 43 links
Collected 44 links
Collected 45 links
Collected 46 links
Collected 47 links
Collected 48 links
Collected 49 links
Collected 50

Truy cập để lấy LINK CỬA HÀNG

In [ ]:
# Đường dẫn file Excel đầu vào chứa cột "Links"
input_file = r"D:/du lieu o cu/HUTECH Courses/NCKH(thầy Hường)/E-Commerce-Data-Analysis/Data Scraping Selenium/Category_Files/store_links.xlsx"

# Đọc file Excel bằng pandas
df = pd.read_excel(input_file)
# Giả sử file Excel có cột "Links" chứa các URL cần truy cập
links = df["Links"].tolist()

# Sử dụng set để lưu các seller link không trùng lặp
seller_links_set = set()

# Khởi tạo Selenium WebDriver (ở đây dùng Chrome)
driver = webdriver.Chrome()
driver.maximize_window()  # Phóng to cửa sổ trình duyệt
driver.implicitly_wait(10)  # Chờ tối đa 10 giây cho các phần tử xuất hiện

# Duyệt qua từng URL trong danh sách
for url in links:
    try:
        print(f"Đang truy cập: {url}")
        driver.get(url)
        # Cho trang load dữ liệu (tùy chỉnh thời gian chờ nếu cần)
        time.sleep(2)
        
        # Tìm phần tử chứa seller link theo cấu trúc HTML được cung cấp.
        # Ta có thể sử dụng CSS selector. Trong HTML mẫu, seller link nằm trong thẻ <a> bên trong div có class:
        # "SellerName__SellerNameStyled-sc-5d1cxl-0 myqYs"
        seller_element = driver.find_element(By.CSS_SELECTOR, "div.SellerName__SellerNameStyled-sc-5d1cxl-0.myqYs a")
        
        # Lấy thuộc tính href của thẻ <a>
        seller_href = seller_element.get_attribute("href")
        print(f"  => Seller link: {seller_href}")
        
        # Thêm vào set để tránh trùng lặp
        seller_links_set.add(seller_href)
    except NoSuchElementException:
        # Nếu không tìm thấy phần tử chứa seller link
        print(f"  => Không tìm thấy seller link trên trang: {url}")
    except Exception as e:
        print(f"  => Lỗi khi xử lý {url}: {e}")

# Đóng trình duyệt
driver.quit()

# Chuyển set thành danh sách để lưu vào file Excel
seller_links_list = list(seller_links_set)

# Lưu kết quả thu thập được vào file Excel mới
output_file = r"D:/du lieu o cu/HUTECH Courses/NCKH(thầy Hường)/E-Commerce-Data-Analysis/Data Scraping Selenium/Category_Files/store_seller_links.xlsx"
output_df = pd.DataFrame({"Seller Links": seller_links_list})
output_df.to_excel(output_file, index=False)

print(f"\nĐã lưu danh sách seller link vào file: {output_file}")


Đang truy cập: https://tiki.vn/card-pci-ra-2-com-9-express-unitek-y-7504-hang-chinh-hang-p46793435.html?spid=56562864
  => Không tìm thấy seller link trên trang: https://tiki.vn/card-pci-ra-2-com-9-express-unitek-y-7504-hang-chinh-hang-p46793435.html?spid=56562864
Đang truy cập: https://tiki.vn/may-ep-cham-mini-may-ep-cham-trai-cay-arber-mec2068md-mau-do-tre-trung-van-phuong-shop-p180394321.html?spid=251009577
  => Seller link: https://tiki.vn/cua-hang/telovietnam?source_screen=product_detail&source_engine=organic
Đang truy cập: https://tiki.vn/rem-che-nang-xe-toyota-vios-2019-2020-hang-loai-1-mr-o-to-p141962576.html?spid=141962577
  => Seller link: https://tiki.vn/cua-hang/rem-che-nang-thiet-ke-theo-xe-mroto?source_screen=product_detail&source_engine=organic
Đang truy cập: https://tka.tiki.vn/pixel/pixel?data=Scwt3jGH9EurOR9rNvvNGpEOJl7wN4znsSMvgTTdWc-HgRgd-TlNjgEcprfYFqqf2d0rKgG1dLjbkRK6bJDlVU0x1hys6kLAbdgcCzyYBdxJzKgkNOTounDfEDzeqOBnQsNfFMbAp4q3GYrYv0WwgKII_eH7J1HlM9Mn9ZLIOb37sSzYmy

In [1]:
import pandas as pd
import threading
from concurrent.futures import ThreadPoolExecutor
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.common.exceptions import NoSuchElementException, TimeoutException
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from openpyxl import load_workbook

# Đường dẫn file Excel
input_file = r"D:/du lieu o cu/HUTECH Courses/NCKH(thầy Hường)/E-Commerce-Data-Analysis/Data Scraping Selenium/Category_Files/store_links.xlsx"
output_file = r"D:/du lieu o cu/HUTECH Courses/NCKH(thầy Hường)/E-Commerce-Data-Analysis/Data Scraping Selenium/Category_Files/store_seller_links.xlsx"

# Đọc file Excel và lấy 20 dòng đầu tiên
df = pd.read_excel(input_file)
links = df["Links"].tolist()[:10]

# Sử dụng tập hợp để tránh trùng lặp seller links
seller_links_set = set()

# Khóa để đảm bảo ghi file an toàn khi dùng đa luồng
lock = threading.Lock()

# Hàm xử lý từng link
def process_link(url):
    global seller_links_set

    # Khởi tạo Selenium WebDriver trong từng luồng
    driver = webdriver.Chrome()
    driver.maximize_window()
    driver.implicitly_wait(10)

    try:
        print(f"Đang truy cập: {url}")
        driver.get(url)

        # Chờ trang load hoàn toàn (timeout 10s)
        WebDriverWait(driver, 10).until(
            EC.presence_of_element_located((By.CSS_SELECTOR, "div.SellerName__SellerNameStyled-sc-5d1cxl-0.myqYs a"))
        )

        # Tìm seller link
        seller_element = driver.find_element(By.CSS_SELECTOR, "div.SellerName__SellerNameStyled-sc-5d1cxl-0.myqYs a")
        seller_href = seller_element.get_attribute("href")
        print(f"  => Seller link: {seller_href}")

        # Dùng khóa để đảm bảo an toàn khi ghi file
        with lock:
            if seller_href not in seller_links_set:
                seller_links_set.add(seller_href)

                # Đọc file hiện tại (nếu có)
                try:
                    existing_df = pd.read_excel(output_file)
                except FileNotFoundError:
                    existing_df = pd.DataFrame(columns=["Seller Links"])

                # Thêm dữ liệu mới
                new_df = pd.DataFrame({"Seller Links": [seller_href]})
                final_df = pd.concat([existing_df, new_df], ignore_index=True)

                # Ghi vào file Excel
                with pd.ExcelWriter(output_file, mode="w", engine="openpyxl") as writer:
                    final_df.to_excel(writer, index=False)

    except TimeoutException:
        print(f"  => Trang {url} load quá lâu, bỏ qua.")
    except NoSuchElementException:
        print(f"  => Không tìm thấy seller link trên trang: {url}")
    except Exception as e:
        print(f"  => Lỗi khi xử lý {url}: {e}")
    finally:
        driver.quit()

# Sử dụng ThreadPoolExecutor để chạy đa luồng
max_threads = 5  # Số luồng tối đa có thể điều chỉnh
with ThreadPoolExecutor(max_workers=max_threads) as executor:
    executor.map(process_link, links)

print(f"\n✅ Đã hoàn thành và lưu danh sách seller link vào file: {output_file}")


Đang truy cập: https://tiki.vn/may-ep-cham-mini-may-ep-cham-trai-cay-arber-mec2068md-mau-do-tre-trung-van-phuong-shop-p180394321.html?spid=251009577
Đang truy cập: https://tiki.vn/rem-che-nang-xe-toyota-vios-2019-2020-hang-loai-1-mr-o-to-p141962576.html?spid=141962577
Đang truy cập: https://tka.tiki.vn/pixel/pixel?data=Scwt3jGH9EurOR9rNvvNGpEOJl7wN4znsSMvgTTdWc-HgRgd-TlNjgEcprfYFqqf2d0rKgG1dLjbkRK6bJDlVU0x1hys6kLAbdgcCzyYBdxJzKgkNOTounDfEDzeqOBnQsNfFMbAp4q3GYrYv0WwgKII_eH7J1HlM9Mn9ZLIOb37sSzYmycoQJK2UhT2gq2c715VzC4jBLzwxGmaHj5_6sWglaAkzZ_ERP1vkgq9WlMVbhQR4cPEq8zR_GqWht5omioSmsQ1aqHm8rPGt-7Of0prj4u1nfDKQFXeeLOVTJB-qEW9iwK7624kJCRKW8Cnxd8b2cJF5UsdIIGC2aJxAWnHNmp5IiEBkuAQlZv_UrafSJTgFtqaGFOcbhm8yamwcyMC1SWjXVxcO74f2QouvBmabuPE7Q27rVeBv5r8NLpaueZ9vo7_prjN-s88VbLST_zd2IXAQQsY04aJ0Xpe3mHEYAQxxKTf1A1xskpD1b7wx8bsKZu5HdrZUHiG5Akw6HZ7NAEkl3zljUjJXwpZtDqAwSLEg0Yz0F7hho1uwIDYx2DPwTCB-4g9rrYw5UzSDGB-xoRWKNaDQbUzJWtP-QlAr-zHNSelbwwIWyN6TFTp0hrOMwWNC9scCwfOdNmkF-47TKW19d4AFVlQzt0Fha1KElAIkA3rPuQNmnR